In [1]:
#SI CARBON PRICE (Readme)
#------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

#Note that this model requires ICE ECX contract data from S&P Capital IQ, which is available under commercial license. For running this code without access to the commercial data comment out the rows referring to historical pricing

# Module conducts the following analysis:

# ---- Supplementary Figure 7: Carbon price projections in EUR t-1 CO2 equivalents


# Module is input for:

# ---- NA

In [2]:
#SET-UP
#------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

check_and_load <- function(packages) {
  for (pkg in packages) {
    if (!requireNamespace(pkg, quietly = TRUE)) {
      message(paste("Installing missing package:", pkg))
      install.packages(pkg, dependencies = TRUE, repos = "https://cloud.r-project.org")
    }
    suppressPackageStartupMessages(library(pkg, character.only = TRUE))
  }
}

required_packages <- c(
  "sf", "dplyr", "readr", "readxl", "jsonlite",
  "giscoR", "geosphere", "stringdist", "data.table",
  "ggplot2", "ggsci", "lubridate"
)
check_and_load(required_packages)

Sys.setenv(PROJ_LIB = "/opt/conda/share/proj")


In [3]:
#INPUTS AND SETTINGS
#------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

# parameters
cutoff_date <- as.Date("2025-01-01")
exchange_rate <- 1 / 1.0321

# default scenario
df <- tibble::tribble(
  ~Scenario, ~Year, ~Value_USD,
  "Default", 2024, 116.63,
  "Default", 2025, 116.63,
  "Default", 2030, 149.33,
  "Default", 2035, 191.84,
  "Default", 2040, 246.34,
  "Default", 2045, 316.10,
  "Default", 2050, 406.57
) %>%
  mutate(
    Value_EUR = Value_USD * exchange_rate,
    Date = as.Date(paste0(Year, "-01-01"))
  )


In [4]:
#DATAFILES
#------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

# parameters
cutoff_date <- as.Date("2025-01-01")
exchange_rate <- 1 / 1.0321

# default scenario
df <- tibble::tribble(
  ~Scenario, ~Year, ~Value_USD,
  "Default", 2024, 116.63,
  "Default", 2025, 116.63,
  "Default", 2030, 149.33,
  "Default", 2035, 191.84,
  "Default", 2040, 246.34,
  "Default", 2045, 316.10,
  "Default", 2050, 406.57
) %>%
  mutate(
    Value_EUR = Value_USD * exchange_rate,
    Date = as.Date(paste0(Year, "-01-01"))
  )

# load historical pricing
carbon_price_path <- "/home/h1604190/Data/sp-carbon-pricing.xls"
historical_col <- "Carbon Emissions - EUA (ECX) (ICE) Historical Pricing"

raw_hist <- read_xls(carbon_price_path)


In [5]:
#SUPPLEMENTARY FIGURE 7
#------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

# parse daily values
hist_daily <- raw_hist %>%
  mutate(
    Period = as.Date(as.character(Period), format = "%b-%d-%Y"),
    Value_EUR = as.numeric(.data[[historical_col]])
  ) %>%
  filter(!is.na(Period), !is.na(Value_EUR)) %>%
  select(Period, Value_EUR)

# daily → monthly averages
hist_monthly <- hist_daily %>%
  mutate(Month = floor_date(Period, "month")) %>%
  group_by(Month) %>%
  summarise(Value_EUR = mean(Value_EUR), .groups = "drop") %>%
  filter(Month < cutoff_date)

# flat carbon price starting 1.1.2025
flat_df <- tibble(
  Scenario = "Flat",
  Date     = seq(cutoff_date, as.Date("2050-01-01"), by = "1 year"),
  Value_EUR = 65
)

# combine scenarios
df_final <- df %>%
  select(Scenario, Date, Value_EUR) %>%
  bind_rows(flat_df)

# rename factors
df_final$Scenario <- recode(df_final$Scenario,
                            "Default" = "Default",
                            "Flat" = "Flat")

df_final$Scenario <- factor(df_final$Scenario, 
                            levels = c("Default", "Flat"))

# ---- UPDATED COLORS ----
color_hist     <- "#555555"                           # dark grey
color_default  <- ggsci::pal_npg("nrc")(10)[2]         # blue (formerly historical)
color_flat     <- ggsci::pal_tron("legacy")(7)[4]      # teal-blue

# rename historical
hist_monthly$Scenario <- "Historical Pricing (ICE ECX contracts)"

# palette
scenario_palette <- c(
  "Default" = color_default,
  "Flat" = color_flat,
  "Historical Pricing (ICE ECX contracts)" = color_hist
)

# plot
supplementary_figure_7 <- ggplot() +
  geom_line(
    data = hist_monthly,
    aes(x = Month, y = Value_EUR, color = Scenario),
    linewidth = 0.9,
    alpha = 1
  ) +
  geom_point(
    data = hist_monthly,
    aes(x = Month, y = Value_EUR, color = Scenario),
    size = 1.8,
    alpha = 0.9
  ) +
  geom_line(
    data = df_final,
    aes(x = Date, y = Value_EUR, color = Scenario),
    linewidth = 1.3
  ) +
  geom_point(
    data = df_final,
    aes(x = Date, y = Value_EUR, color = Scenario),
    size = 3
  ) +
  scale_color_manual(values = scenario_palette) +
  labs(
    title = "CO₂ Price Trajectories and Historical EUA Pricing",
    x = "Year",
    y = "CO₂ Price (EUR/tCO₂)",
    color = NULL
  ) +
  scale_x_date(
    date_breaks = "2 years",
    date_labels = "%Y",
    sec.axis = dup_axis(name = NULL, labels = NULL)
  ) +
  scale_y_continuous(sec.axis = dup_axis(name = NULL, labels = NULL)) +
  theme_minimal(base_size = 18) +
  theme(
    axis.line   = element_line(color = "black"),
    axis.ticks  = element_line(color = "black"),
    axis.text   = element_text(size = 18),
    axis.title  = element_text(size = 20),
    plot.title  = element_text(size = 20, hjust = 0.5),

    # fewer gridlines
    panel.grid.minor = element_blank(),
    panel.grid.major.y = element_line(color = "grey85", linewidth = 0.3),
    panel.grid.major.x = element_line(color = "grey92", linewidth = 0.2),

    legend.position = "bottom",
    legend.text     = element_text(size = 18),

    axis.text.x.top    = element_blank(),
    axis.text.y.right  = element_blank(),
    axis.ticks.x.top   = element_blank(),
    axis.ticks.y.right = element_blank()
  )

options(repr.plot.width=20, repr.plot.height=10, repr.plot.res=800)
supplementary_figure_7

ggsave("supplementary-figure-7.pdf",supplementary_figure_7, device = cairo_pdf,width = 12, height = 8,units = "in",dpi = 800)